# Bayesian spectral reconstruction with MC-Stan

This notebook implements spectral function reconstruction using the BR method (alternatively Tikhonov, MEM, etc.) in a fully Bayesian fashion by constructing and sampling the full posterior of the $N_\omega$  parameters $\rho_l$ based on the supplied $N_\tau$ datapoints. In addition we also self consistently estimate the hyperparameter posterior $P(\alpha|D)$ using an uninformative hyperprior $P(\alpha)\sim LogNormal$.


# Import the necessary libraries 

In [ ]:
#Numerical Routines and arrays
import numpy as np

#Graph Plotting
import matplotlib.pyplot as plt
import matplotlib.mlab as mlab

#Curve fitting for Autocorrelations
from scipy.optimize import curve_fit

#Statistical Analysis of MCStan output
import arviz as az
import xarray as xr
xr.set_options(display_expand_data=False, display_expand_attrs=False);

# Initiate Stan via cmdstanpy (Python interface for cmdstan)

In [ ]:
import os
from cmdstanpy import CmdStanModel, cmdstan_path

# Read-in of T=0 Lattice QCD data

In [ ]:
Nmeas=400
filelist= ["./TstDataNRQCDb66641SBottom/32x32_31."+ str(k)  for k in range(1,Nmeas+1)];
RawCorrelators = [np.loadtxt(f, skiprows=0) for f in filelist]
print(RawCorrelators[4])

The datapoint at $\tau=0$ only provides overall normalization and we are not going to include it in the analysis 

In [ ]:
DataArrayIndiv=np.column_stack(RawCorrelators[k][1:,2] for k in range(Nmeas))

# Check the histograms of individual datapoints

In [ ]:
F01=plt.figure()
plt.yscale('linear')
plt.xlabel('$D(\\tau/a=1)$', fontsize=14)
plt.ylabel('$N_{realizations}$', fontsize=14)
plt.title('Input Data Histogram')
plt.hist(DataArrayIndiv[1],bins=50);
plt.show()
F01.savefig("D1Histogram.pdf",bbox_inches='tight')

# Compute the mean and the covariance matrix 
note that we are computing the covariance matrix w.r.t. the mean hich has an additional factor 1/N in it 

In [ ]:
DataAverage=np.average(DataArrayIndiv,axis=1)
print(DataAverage.shape)
print(DataAverage)
Nt=len(DataAverage)
print(Nt)

Note that in general lattice QCD data will contain **autocorrelations**, which need to be estimated for an accurate determination of the actual data uncertainties.

In [ ]:
AutoCorr= [ np.fft.ifft(np.absolute(np.fft.fft( DataArrayIndiv[k] - DataAverage[k]  ))) for k in range( Nt ) ]

AutoCorrNrm= [ np.real(AutoCorr[k]) /np.real(AutoCorr[k][0]) for k in range( Nt ) ]

plt.xlabel('$n_{mc}$', fontsize=14)
plt.ylabel('$AC(n)$', fontsize=14)
plt.title('AutoCorrelation time')
plt.xlim([0, 20])
plt.plot(range(len(AutoCorrNrm[1])), AutoCorrNrm[1])
plt.plot(range(len(AutoCorrNrm[5])), AutoCorrNrm[5])
plt.plot(range(len(AutoCorrNrm[10])), AutoCorrNrm[10])
plt.show()

We estimate the autocorrelation times by fitting the autocorrelation function. This estimate tells us how many subsequent lattice configurations are still significantly correlated, providing a correction factor for the covariance matrix estimate below.

In [ ]:
def Exp_func(x : float , b : float ) -> float:
    y=np.exp(- (1/b) * x )
    return y

athresh=0.05

AutoCorrFactors=np.ones_like(range(Nt), dtype=np.float64)
AutoCorrFits=np.ones_like(range(Nt), dtype=np.float64)
    
for j in range(0,Nt):
    afitparm, afitcorr = curve_fit(Exp_func, range(0,len(AutoCorrNrm[j])) , np.real(AutoCorrNrm[j]));
    AutoCorrFactors[j]=np.ceil(-np.log(athresh)*afitparm[0]);
    AutoCorrFits[j]=afitparm[0];
    #print(afitparm)
   
print(AutoCorrFactors);

In [ ]:
# This input data requires adjustment of the autocorrelation by a factor 4. Make sure to set to unity when using
# your own lattice QCD data set.

AutoCorrelationCorr=4.;
DataCovarianceMatrix=AutoCorrelationCorr*np.array([[ AutoCorrFactors[i]*AutoCorrFactors[j]*sum( np.array([ ( DataArrayIndiv[i][n]-DataAverage[i] )*
                                     ( DataArrayIndiv[j][n]-DataAverage[j] )/((Nmeas-1.)*Nmeas) for n in range(Nmeas)]) )
                  for i in range(Nt) ] for j in range(Nt)]);
print(DataCovarianceMatrix.shape)
print(DataCovarianceMatrix)

In [ ]:
print(np.sqrt(DataCovarianceMatrix.diagonal()))

# Plot the correlator with naive errobars

In [ ]:
plt.yscale('log')
plt.xlabel('$\\tau/a$', fontsize=14)
plt.ylabel('$^3S_1(b\\bar b)$  $D( \\tau )$', fontsize=14)
plt.title('Input Data')
plt.errorbar(range(1,32), DataAverage, yerr=np.sqrt(DataCovarianceMatrix.diagonal()) , fmt='--o' )
plt.show()

# Decorrelate the data in preparation for the Bayesian analysis
This requires to first compute the eigenvalues and eigenvectors of the covariance matrix and then transofrming the data to the basis in which the covariance matrix is diagonal.

In [ ]:
DiagCorrVar,UInv=np.linalg.eig(DataCovarianceMatrix)
print(  UInv.conj().T @ DataCovarianceMatrix @ UInv )

In [ ]:
DCDataAvg= UInv.conj().T @ DataAverage;
print(DCDataAvg)

In [ ]:
print(np.sqrt(DiagCorrVar))

# Check the form of the distribution of the data after decorrelation

In [ ]:
 DataArrayIndivPostTrans=np.column_stack( UInv.conj().T @ RawCorrelators[k][1:,2] for k in range(200))

In [ ]:
plt.hist(DataArrayIndivPostTrans[1]);
plt.show()

# Setup of the Bayesian reconstruction by sepcifying the inference model

We first need to construct the spectral representation that underlies the observed data. This "model" is provided by ab-initio QCD and thus does not carry uncertainty in our analysis.

We discretize the spectral function with Nw steps between a minimum wmin and maximum wmax frequency.

In the case of T=0 hadron correlator data the appropriate kernel is $K(\omega,\tau)=exp(-\omega\tau)$.

In [ ]:
Nw=250;

# BEWARE: You will need Nw>1000 for an accurate reconstruction of the different peak features 
# Nw=250 set just for a first quick check of the approach.

wmin=0.0001;
wmax=6.;
dw=(wmax-wmin)/Nw;

omegas= [ wmin+k*dw for k in range(0,Nw)]


Kernel=np.array([[  (1./2. if w == 0 or w== Nw-1 else 1.) * 
                    dw*np.exp(-(wmin+dw*w)*t) 
                  for w in range(Nw) ] for t in range(1,Nt+1)]);
print(Kernel.shape)

We already transform the kernel into the same basis in which the decorrelated data has been expressed in (independent Gaussians)

In [ ]:
DCKernel= UInv.conj().T @ Kernel;
print(DCKernel)

# Setup the PySTAN model for the BR method

We have decorrelated the data, so that the model can be formulated with independent Gaussian distributions. This inference task will still be challenging for the HMC since the Kernel has many vanishing singular values.

In [ ]:
# Note that in the model below I have used a constant uncertainty \alpha. In a full analysis one would
# promote \alpha to an array and assign a hyperprior to each.

stan_model_BR = """
data {
    real dw;
    int sNt;  // Number of datapoints
    int sNw;  // Number of parameters, i.e. spectral function
    matrix[sNt, sNw] Kernel;
    vector[sNt] D;  // Simulation data
    vector[sNt] Uncertainty;  // Uncertainty
    vector[sNw] DefMod;  // DefaultModel
}
parameters {
    vector<lower=0>[sNw] rho;  // Parameters, i.e spectral function
    real<lower=0> alpha;  // Hyperparameter
}
model {

    alpha ~ lognormal(0.,20); // Broad hyperprior that allows alpha to be sampled over relevant range
    
    for (n in 1:sNw)
        rho[n] ~ gamma(alpha*dw+1, alpha*dw/DefMod[n]);  // BR prior, which is the gamma distribution

    D ~ normal(Kernel * rho, Uncertainty); // Gaussian likelihood

}
"""
with open("modelBR_rec.stan", "w") as file:
    file.write(stan_model_BR)

In [ ]:
BR_rec=CmdStanModel(stan_file='./modelBR_rec.stan', cpp_options={'STAN_THREADS':'true'});

# Set the default model
In the absence of any explicit prior information on the value of, rho we choose the uninformative constant default model.

In [ ]:
m=[1 for i in range(Nw)];

# Prepare and execute the MC STAN posterior sampling

In [ ]:
SpecRecData={'dw': dw, 'sNt': Nt, 'sNw': Nw, 'Kernel': DCKernel, 
          'D': DCDataAvg, 'Uncertainty': np.sqrt(DiagCorrVar), 'DefMod': m }

In [ ]:
Niter=1000;
Nwarmup=250;
Nchain=4

# For a useful spectral function reconstruction in case of this lattice QCD data, you will need
# at least Niter=2500; Nwarmup=500; Nchain=40

In [ ]:
MCBR_rec = BR_rec.sample(data=SpecRecData, chains=40, parallel_chains=4, show_console=True, iter_warmup=Nwarmup, iter_sampling=Niter)


# Inspect the posterior for the individual spectral function bins and the uncertatinty parameter
Note that due to modelling of the uncertatinty we can obtain an estimate of the strength of regularization provided by inspecting the posterior for the alpha parameter.

In [ ]:
az.plot_posterior(MCBR_rec, var_names=['rho'], kind='hist')

In [ ]:
az.plot_posterior(MCBR_rec, var_names=['alpha'], kind='hist')

# Convert xdata array to numpy array for further processing

In [ ]:
cmdstanpy_dataBR = az.from_cmdstanpy(posterior=MCBR_rec);

In [ ]:
BR_Rho_posterior=cmdstanpy_dataBR.posterior["rho"].to_numpy();
BR_Alpha_posterior=cmdstanpy_dataBR.posterior["alpha"].to_numpy();

In [ ]:
WhichFrequencyBin=100;
Chain=20;

F01=plt.figure()
plt.yscale('linear')
plt.xlabel('$\\rho(\\omega a$'+"="+str(omegas[WhichFrequencyBin])+")", fontsize=14)
plt.ylabel('$N_{realizations}$', fontsize=14)
plt.title('Rho Histogram at single frequency')
plt.hist(np.transpose(BR_Rho_posterior[Chain])[WhichFrequencyBin],bins=50);
plt.show()
F01.savefig("RhoSingleHistogram.pdf",bbox_inches='tight')

In [ ]:
F01=plt.figure()
plt.yscale('linear')
plt.xlabel('$\\alpha(\\omega a$'+"="+str(omegas[WhichFrequencyBin])+")", fontsize=14)
plt.ylabel('$N_{realizations}$', fontsize=14)
plt.title('Alpha Marginal Posterior Histogram')
plt.hist(np.transpose(BR_Alpha_posterior[Chain]),bins=100);
plt.show()
F01.savefig("AlphaSingleHistogram.pdf",bbox_inches='tight')

# Now inspect the reconstructed spectral function
I.e. we produce a point estimate from the posterior distribution with a naive standard deviation error

In [ ]:
BR_Rho_PointEst=[ np.mean(np.transpose(BR_Rho_posterior[2:])[c]) for c in range (Nw)]
BR_Rho_Std=[ np.std(np.transpose(BR_Rho_posterior[2:])[c]) for c in range (Nw)]/np.sqrt(Niter*Nchain)

In [ ]:
F2=plt.figure()
plt.yscale('linear')
plt.xlabel('$\\omega a$', fontsize=14)
plt.ylabel('$^3S_1(b\\bar b)$  $\\rho( \\omega )$', fontsize=14)
plt.title('Spectral reconstruction')
plt.errorbar(omegas, BR_Rho_PointEst, yerr=BR_Rho_Std, label='PstMAP',fmt='o')
plt.legend(loc='upper right', shadow=True, fontsize='large')
plt.show()
F2.savefig("SpectralREconstruction.pdf",bbox_inches='tight')

In [ ]:
F2=plt.figure()
plt.yscale('linear')
plt.xlabel('$\\omega a$', fontsize=14)
plt.ylabel('$^3S_1(b\\bar b)$  $\\rho( \\omega )$', fontsize=14)
plt.title('Spectral reconstruction')
plt.plot(omegas, BR_Rho_PointEst, label='PstMean')
plt.legend(loc='upper right', shadow=True, fontsize='large')
plt.show()
F2.savefig("PstMean.pdf",bbox_inches='tight')

In [ ]:
ReconstrData=Kernel@BR_Rho_PointEst

In [ ]:
F4=plt.figure()
plt.yscale('linear')
plt.xlabel('$\\tau/a$', fontsize=14)
plt.ylabel('$^3S_1(b\\bar b)$  $D( \\tau )$', fontsize=14)
plt.title('Input Data')
plt.errorbar(range(0,31), np.abs(DataAverage-ReconstrData)/DataAverage , fmt='--o', label="Rec vs. Input rel. err." )
plt.errorbar(range(0,31), np.sqrt(DataCovarianceMatrix.diagonal())/DataAverage , fmt='r--o', label="Uncertainty on Input")
plt.legend(loc='upper left', shadow=True, fontsize='large')
plt.show()
F4.savefig("ComparisonDataRecErr.pdf",bbox_inches='tight')